In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
pip install pyproj

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 6.3 MB 16.1 MB/s 


In [ ]:
import json
import os
from tqdm import tqdm
import pickle

from shapely.geometry import Polygon, shape
import pyproj
from pyproj import Proj

import pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from numpy import random
from tqdm import tqdm
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from imblearn import pipeline
from sklearn.feature_selection import SelectKBest, f_regression, f_classif, chi2, SelectFromModel
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.cluster import KMeans
from sklearn.tree import DecisionTreeRegressor, DecisionTreeClassifier
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from scipy.stats import pearsonr
from sklearn.metrics import confusion_matrix, classification_report, silhouette_score
from sklearn.svm import SVR, LinearSVR, SVC, LinearSVC
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.preprocessing import StandardScaler, MinMaxScaler, OneHotEncoder
from sklearn.kernel_approximation import Nystroem
from sklearn.linear_model import SGDClassifier, SGDRegressor
from sklearn.neural_network import MLPClassifier, MLPRegressor
from scipy import stats
from keras.layers import Dense
from keras.models import Sequential
from sklearn.metrics import plot_confusion_matrix, auc
from sklearn.impute import SimpleImputer

In [ ]:
pip install area

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Created wheel for area: filename=area-1.1.1-py3-none-any.whl size=3626 sha256=439f4d6d167c53a0046e5f529809217302430250b93715104dcbb7cbc837cbef
  Stored in directory: /root/.cache/pip/wheels/59/e8/a2/0a9be8239358f5e3b48e1b5cb756f98b0f992b881e1b8b21b2
Successfully built area


In [ ]:
vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong.pickle', 'rb'))
blob_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_centroids.pickle','rb'))
blob_intensities = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_intensities.pickle','rb'))
blob_areas = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_areas.pickle','rb'))

In [ ]:
len(blob_cen)

3819

In [ ]:
type(blob_cen) 

list

In [ ]:
blob_cen[0] , blob_intensities[0] , blob_areas[0]

([75.0758015550049, 18.895163686170015], 6.170222759246826, 0.9977632945405001)

In [ ]:
min(blob_intensities) , min(blob_areas)

(3.818061351776123, 0.9977632945385269)

In [ ]:
max(blob_intensities) , max(blob_areas)

(948.4654541015625, 1340.9938678625947)

## Viirs

In [ ]:
#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_viirs_updated_2012.geojson'


dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2019.geojson'


f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
len(data['features'])

7961

In [ ]:
min(blob_areas)

0.9977632945385269

In [ ]:
blob_intensities[0]

6.170222759246826

In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)




In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 79.85027234554931 Y: 26.354693052025908
 Intensity: 6.099999904632568
{'geometry': {'coordinates': [[[79.89159484861878, 26.476863930666163], [79.91854430714241, 26.476863930666163], [79.91854430714241, 26.48584708350736], [79.9095611543012, 26.48584708350736], [79.9095611543012, 26.494830236348555], [79.89159484861878, 26.494830236348555], [79.89159484861878, 26.476863930666163]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '7247', 'properties': {'mean': 5.393500089645386, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :4.457075058528114
Area2 :4.475257702270763
POLYGON ((79.89159484861878 26.47686393066616, 79.91854430714241 26.47686393066616, 79.91854430714241 26.48584708350736, 79.9095611543012 26.48584708350736, 79.9095611543012 26.49483023634856, 79.89159484861878 26.49483023634856, 79.89159484861878 26.47686393066616))
shapely Method POINT (79.90327294731235 26.48494876822324)
Centroid X: 79.90442792410622 Y: 

In [ ]:


len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(7961, 7961, 7961)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.033750057220459, 0.8207103399652012)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(270.75, 1461.9729126409825)

#### Without Only

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 




scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['none','size', 'size_intensity', 'intensity']

result_comb = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

    
      
      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      res = np.max(res, axis=0)
      result_comb[j,start:end] = res
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.16265126 34.64614312]


 27%|██▋       | 95/346 [01:29<03:58,  1.05it/s]

In [ ]:
result_comb_df

dc_score_none_none  ...  dc_score_sqrt_intensity
village_id                      ...                         
628551.0              0.173579  ...                 2.609036
628556.0              0.103018  ...                 2.734730
628553.0              0.143336  ...                 2.590991
628554.0              0.112110  ...                 2.670639
628632.0              0.054273  ...                 2.946274
...                        ...  ...                      ...
209407.0              0.109232  ...                 1.002760
209403.0              0.099752  ...                 1.034285
209411.0              0.093952  ...                 1.038321
209412.0              0.102064  ...                 1.054749
209417.0              0.111613  ...                 1.068424

[345511 rows x 12 columns]

#### Only 

In [ ]:

scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['size', 'size_intensity', 'intensity']

result_comb_2 = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

      ids = np.argmax(res, axis=0)
      
      if ws == 'size':
        res = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'size_intensity':
        res = np.tile((area_arr*intensity_arr).reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'intensity':
        res = np.tile(intensity_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]

      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      result_comb_2[j,start:end] = res  
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}_only'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res_2 = np.append(vill_ids_arr, result_comb_2.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df_2 = pd.DataFrame(final_res_2, columns=columns)
result_comb_df_2 = result_comb_df_2.set_index('village_id')
print(result_comb_df_2)

100%|██████████| 346/346 [04:39<00:00,  1.24it/s]

['village_id', 'dc_score_none_size_only', 'dc_score_none_size_intensity_only', 'dc_score_none_intensity_only', 'dc_score_log_size_only', 'dc_score_log_size_intensity_only', 'dc_score_log_intensity_only', 'dc_score_sqrt_size_only', 'dc_score_sqrt_size_intensity_only', 'dc_score_sqrt_intensity_only']
(345511, 1)
(345511, 13)
            dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0                 343.894595  ...                      4.095577
628556.0                 343.894595  ...                      4.093898
628553.0                 343.894595  ...                      4.095577
628554.0                 343.894595  ...                      4.093898
628632.0                 343.894595  ...                      4.093898
...                             ...  ...                           ...
209407.0                1268.879142  ...                      5.042603
209403.0                1268.879142 

In [ ]:
result_comb_df_2

dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0                 313.859800  ...                     17.564239
628556.0                 313.859800  ...                     17.564239
628553.0                 313.859800  ...                     17.564239
628554.0                 313.859800  ...                     17.564239
628632.0                 313.859800  ...                     17.564239
...                             ...  ...                           ...
209407.0                 870.175829  ...                      4.797450
209403.0                  94.514181  ...                      4.797450
209411.0                  94.514181  ...                      4.797450
209412.0                  94.514181  ...                      4.797450
209417.0                  94.514181  ...                      4.797450

[345511 rows x 9 columns]

#### Combine the two

In [ ]:
result_comb_df_final = pd.merge(result_comb_df, result_comb_df_2, left_index=True, right_index=True, how='inner')

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.173579  ...                     17.564239
628556.0              0.103018  ...                     17.564239
628553.0              0.143336  ...                     17.564239
628554.0              0.112110  ...                     17.564239
628632.0              0.054273  ...                     17.564239
...                        ...  ...                           ...
209407.0              0.109232  ...                      4.797450
209403.0              0.099752  ...                      4.797450
209411.0              0.093952  ...                      4.797450
209412.0              0.102064  ...                      4.797450
209417.0              0.111613  ...                      4.797450

[345511 rows x 21 columns]

#### Test Code

In [ ]:
res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

In [ ]:
res.shape

(2690, 1000)

In [ ]:
res_temp = np.max(res,axis=0)

In [ ]:
ids = np.argmax(res,axis=0)

In [ ]:
ids.shape

(1000,)

In [ ]:
ids

array([1453, 1455,  922, 1458,  922, 1459, 2351,  922, 2350, 2351, 1455,
       2527, 1459, 2351, 2527, 1459, 1455,  932, 2351, 2527, 1459, 2354,
       1453, 2527, 1455, 1455, 1458,  932, 1458, 2205, 1455, 2205, 2527,
       1455, 1459, 2205,  922, 2354, 1455,  932, 2354, 2350,  932, 2527,
       2527, 2205, 1459,  922, 2527, 1455, 1459, 1459,  922, 1455,  932,
       1455, 2350, 2350, 1455, 2527, 1459, 2527, 1455, 2351, 2354, 2527,
       1455, 2354, 2354, 2350, 2350, 2351,  922, 2351, 1459, 1455, 1455,
       1455, 2205, 2354, 2205, 1852, 2351, 2352, 1455, 1459, 2527, 2354,
       1455, 1455, 2351, 2350, 2351, 2354, 2354, 2527, 2205, 2205, 1455,
        922, 1455,  932, 1455, 2351, 1453, 2350, 2354, 1852, 2354,  922,
       1453, 1455, 2351, 2351, 2350, 2205, 2354,  932, 2527, 1852, 1455,
       2350, 2351, 1455, 1455, 2205, 2205, 1852, 2205, 2527, 1459,  932,
       1455, 2527, 2527, 2351, 2351, 1455, 1852,  922, 2527, 2351, 2527,
       1455, 2205, 2351, 2527, 2354,  932, 2354,  9

In [ ]:
area_arr.reshape(-1,1).shape

(2690, 1)

In [ ]:
temp = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))

In [ ]:
temp.shape

(2690, 1000)

In [ ]:
temp[[1,2],2]

array([1.88317373, 1.88390845])

In [ ]:
np.tile(np.array([0.1,0.2,0.3,0.5,0.6]).reshape(-1,1),(1,4))[[3,0],np.arange(2)]

array([0.5, 0.1])

In [ ]:
area_arr.shape

(2690,)

In [ ]:
distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled).shape

(2690, 1000)

In [ ]:
print(vill_lat_arr.shape)

(1000,)


#### Results

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.173579  ...                     17.564239
628556.0              0.103018  ...                     17.564239
628553.0              0.143336  ...                     17.564239
628554.0              0.112110  ...                     17.564239
628632.0              0.054273  ...                     17.564239
...                        ...  ...                           ...
209407.0              0.109232  ...                      4.797450
209403.0              0.099752  ...                      4.797450
209411.0              0.093952  ...                      4.797450
209412.0              0.102064  ...                      4.797450
209417.0              0.111613  ...                      4.797450

[345511 rows x 21 columns]

In [ ]:
#pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_viirs_2012.pickle','wb'))

pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/data_2018.pickle','wb'))

In [ ]:
result_viirs_2013 = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/data_2018.pickle','rb'))

In [ ]:
result_viirs_2013

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.173579  ...                     17.564239
628556.0              0.103018  ...                     17.564239
628553.0              0.143336  ...                     17.564239
628554.0              0.112110  ...                     17.564239
628632.0              0.054273  ...                     17.564239
...                        ...  ...                           ...
209407.0              0.109232  ...                      4.797450
209403.0              0.099752  ...                      4.797450
209411.0              0.093952  ...                      4.797450
209412.0              0.102064  ...                      4.797450
209417.0              0.111613  ...                      4.797450

[345511 rows x 21 columns]

## Dmsp

In [ ]:
#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_dmsp_updated_2011.geojson'


dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_dmsp_updated_2013.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
len(data['features'])

5869

In [ ]:
min(blob_areas)

0.9977632945385269

In [ ]:
blob_intensities[0]

6.170222759246826

In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)




In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 77.33312602474189 Y: 11.941446911056188
 Intensity: 5.0
{'geometry': {'coordinates': [[[77.353929115532, 11.848778597536489], [77.353929115532, 11.839795444695294], [77.3449459626908, 11.839795444695294], [77.3449459626908, 11.821829139012904], [77.37189542121439, 11.821829139012904], [77.37189542121439, 11.830812291854098], [77.3629122683732, 11.830812291854098], [77.3629122683732, 11.839795444695294], [77.37189542121439, 11.839795444695294], [77.37189542121439, 11.848778597536489], [77.353929115532, 11.848778597536489]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '5155', 'properties': {'mean': 4.571428571428571, 'nl': 1}, 'type': 'Feature'}
Area1 :6.809143206463413
Area2 :6.851220481552897
POLYGON ((77.353929115532 11.84877859753649, 77.353929115532 11.83979544469529, 77.3449459626908 11.83979544469529, 77.3449459626908 11.8218291390129, 77.37189542121439 11.8218291390129, 77.37189542121439 11.8308122918541, 77.3629122

In [ ]:


len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(5869, 5869, 5869)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(4.0, 0.8233543314955732)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(62.93247446471216, 7193.498012653945)

#### Without Only

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 




scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['none','size', 'size_intensity', 'intensity']

result_comb = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

    
      
      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      res = np.max(res, axis=0)
      result_comb[j,start:end] = res
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.16405229 34.64442725]


100%|██████████| 346/346 [03:16<00:00,  1.76it/s]

['village_id', 'dc_score_none_none', 'dc_score_none_size', 'dc_score_none_size_intensity', 'dc_score_none_intensity', 'dc_score_log_none', 'dc_score_log_size', 'dc_score_log_size_intensity', 'dc_score_log_intensity', 'dc_score_sqrt_none', 'dc_score_sqrt_size', 'dc_score_sqrt_size_intensity', 'dc_score_sqrt_intensity']
(345511, 1)
(345511, 13)
            dc_score_none_none  ...  dc_score_sqrt_intensity
village_id                      ...                         
628551.0              0.129412  ...                 1.969253
628556.0              0.116372  ...                 2.215178
628553.0              0.104115  ...                 1.870624
628554.0              0.111545  ...                 2.168748
628632.0              0.087393  ...                 1.919651
...                        ...  ...                      ...
209407.0              0.067943  ...                 1.461111
209403.0              0.067642  ...                 1.504621
209411.0              0.070995  ...          

In [ ]:
result_comb_df

dc_score_none_none  ...  dc_score_sqrt_intensity
village_id                      ...                         
628551.0              0.129412  ...                 1.969253
628556.0              0.116372  ...                 2.215178
628553.0              0.104115  ...                 1.870624
628554.0              0.111545  ...                 2.168748
628632.0              0.087393  ...                 1.919651
...                        ...  ...                      ...
209407.0              0.067943  ...                 1.461111
209403.0              0.067642  ...                 1.504621
209411.0              0.070995  ...                 1.510126
209412.0              0.077113  ...                 1.532710
209417.0              0.082820  ...                 1.551581

[345511 rows x 12 columns]

#### With Only

In [ ]:

scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['size', 'size_intensity', 'intensity']

result_comb_2 = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

      ids = np.argmax(res, axis=0)
      
      if ws == 'size':
        res = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'size_intensity':
        res = np.tile((area_arr*intensity_arr).reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'intensity':
        res = np.tile(intensity_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]

      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      result_comb_2[j,start:end] = res  
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}_only'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res_2 = np.append(vill_ids_arr, result_comb_2.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df_2 = pd.DataFrame(final_res_2, columns=columns)
result_comb_df_2 = result_comb_df_2.set_index('village_id')
print(result_comb_df_2)

100%|██████████| 346/346 [03:14<00:00,  1.78it/s]

['village_id', 'dc_score_none_size_only', 'dc_score_none_size_intensity_only', 'dc_score_none_intensity_only', 'dc_score_log_size_only', 'dc_score_log_size_intensity_only', 'dc_score_log_intensity_only', 'dc_score_sqrt_size_only', 'dc_score_sqrt_size_intensity_only', 'dc_score_sqrt_intensity_only']
(345511, 1)
(345511, 13)
            dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0               11418.330481  ...                      6.493587
628556.0               11418.330481  ...                      6.493587
628553.0               11418.330481  ...                      6.493587
628554.0               11418.330481  ...                      6.493587
628632.0               11418.330481  ...                      6.493587
...                             ...  ...                           ...
209407.0                1681.159417  ...                      7.174631
209403.0                1681.159417 

In [ ]:
result_comb_df_2

dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0               11418.330481  ...                      6.493587
628556.0               11418.330481  ...                      6.493587
628553.0               11418.330481  ...                      6.493587
628554.0               11418.330481  ...                      6.493587
628632.0               11418.330481  ...                      6.493587
...                             ...  ...                           ...
209407.0                1681.159417  ...                      7.174631
209403.0                1681.159417  ...                      7.174631
209411.0                1681.159417  ...                      7.174631
209412.0                1681.159417  ...                      7.174631
209417.0                1681.159417  ...                      7.174631

[345511 rows x 9 columns]

#### Combine the two

In [ ]:
result_comb_df_final = pd.merge(result_comb_df, result_comb_df_2, left_index=True, right_index=True, how='inner')

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.129412  ...                      6.493587
628556.0              0.116372  ...                      6.493587
628553.0              0.104115  ...                      6.493587
628554.0              0.111545  ...                      6.493587
628632.0              0.087393  ...                      6.493587
...                        ...  ...                           ...
209407.0              0.067943  ...                      7.174631
209403.0              0.067642  ...                      7.174631
209411.0              0.070995  ...                      7.174631
209412.0              0.077113  ...                      7.174631
209417.0              0.082820  ...                      7.174631

[345511 rows x 21 columns]

#### Test Code

In [ ]:
res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

In [ ]:
res.shape

(2690, 1000)

In [ ]:
res_temp = np.max(res,axis=0)

In [ ]:
ids = np.argmax(res,axis=0)

In [ ]:
ids.shape

(1000,)

In [ ]:
ids

array([1453, 1455,  922, 1458,  922, 1459, 2351,  922, 2350, 2351, 1455,
       2527, 1459, 2351, 2527, 1459, 1455,  932, 2351, 2527, 1459, 2354,
       1453, 2527, 1455, 1455, 1458,  932, 1458, 2205, 1455, 2205, 2527,
       1455, 1459, 2205,  922, 2354, 1455,  932, 2354, 2350,  932, 2527,
       2527, 2205, 1459,  922, 2527, 1455, 1459, 1459,  922, 1455,  932,
       1455, 2350, 2350, 1455, 2527, 1459, 2527, 1455, 2351, 2354, 2527,
       1455, 2354, 2354, 2350, 2350, 2351,  922, 2351, 1459, 1455, 1455,
       1455, 2205, 2354, 2205, 1852, 2351, 2352, 1455, 1459, 2527, 2354,
       1455, 1455, 2351, 2350, 2351, 2354, 2354, 2527, 2205, 2205, 1455,
        922, 1455,  932, 1455, 2351, 1453, 2350, 2354, 1852, 2354,  922,
       1453, 1455, 2351, 2351, 2350, 2205, 2354,  932, 2527, 1852, 1455,
       2350, 2351, 1455, 1455, 2205, 2205, 1852, 2205, 2527, 1459,  932,
       1455, 2527, 2527, 2351, 2351, 1455, 1852,  922, 2527, 2351, 2527,
       1455, 2205, 2351, 2527, 2354,  932, 2354,  9

In [ ]:
area_arr.reshape(-1,1).shape

(2690, 1)

In [ ]:
temp = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))

In [ ]:
temp.shape

(2690, 1000)

In [ ]:
temp[[1,2],2]

array([1.88317373, 1.88390845])

In [ ]:
np.tile(np.array([0.1,0.2,0.3,0.5,0.6]).reshape(-1,1),(1,4))[[3,0],np.arange(2)]

array([0.5, 0.1])

In [ ]:
area_arr.shape

(2690,)

In [ ]:
distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled).shape

(2690, 1000)

In [ ]:
print(vill_lat_arr.shape)

(1000,)


#### Results

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.129412  ...                      6.493587
628556.0              0.116372  ...                      6.493587
628553.0              0.104115  ...                      6.493587
628554.0              0.111545  ...                      6.493587
628632.0              0.087393  ...                      6.493587
...                        ...  ...                           ...
209407.0              0.067943  ...                      7.174631
209403.0              0.067642  ...                      7.174631
209411.0              0.070995  ...                      7.174631
209412.0              0.077113  ...                      7.174631
209417.0              0.082820  ...                      7.174631

[345511 rows x 21 columns]

In [ ]:
pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_dmsp_2011.pickle','wb'))

In [ ]:
result_dmsp_2011 = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_dmsp_2011.pickle','rb'))

In [ ]:
result_dmsp_2011

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.129412  ...                      6.493587
628556.0              0.116372  ...                      6.493587
628553.0              0.104115  ...                      6.493587
628554.0              0.111545  ...                      6.493587
628632.0              0.087393  ...                      6.493587
...                        ...  ...                           ...
209407.0              0.067943  ...                      7.174631
209403.0              0.067642  ...                      7.174631
209411.0              0.070995  ...                      7.174631
209412.0              0.077113  ...                      7.174631
209417.0              0.082820  ...                      7.174631

[345511 rows x 21 columns]

## Viirs_extended_time_series

In [ ]:
#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_viirs_updated_2012.geojson'


#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_viirs_updated_2013.geojson'


dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2011.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
len(data['features'])

2829

In [ ]:
min(blob_areas)

0.9977632945385269

In [ ]:
blob_intensities[0]

6.170222759246826

In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)




In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 75.77239515143489 Y: 31.21046736618144
 Intensity: 14.390136419900783
{'geometry': {'coordinates': [[[78.62504524256113, 18.83767151957523], [78.63402839540228, 18.83767151957523], [78.63402839540228, 18.846654672416427], [78.62504524256113, 18.846654672416427], [78.62504524256113, 18.83767151957523]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '2115', 'properties': {'mean': 7.3456878662109375, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :0.9413904129336101
Area2 :0.9464118524042785
POLYGON ((78.62504524256113 18.83767151957523, 78.63402839540228 18.83767151957523, 78.63402839540228 18.84665467241643, 78.62504524256113 18.84665467241643, 78.62504524256113 18.83767151957523))
shapely Method POINT (78.62953681898172 18.84216309599583)
Centroid X: 78.62863850369759 Y: 18.841264780711708
 Intensity: 7.3456878662109375
{'geometry': {'coordinates': [[[78.71487677097306, 18.810722061051642], [78.72385992381427, 18.81072

In [ ]:


len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(2829, 2829, 2829)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.0188665390014648, 0.8264619363154188)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(114.45814743041993, 724.1482295977323)

#### Without Only

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 




scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['none','size', 'size_intensity', 'intensity']

result_comb = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

    
      
      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      res = np.max(res, axis=0)
      result_comb[j,start:end] = res
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.04697186 34.12209775]


100%|██████████| 346/346 [01:58<00:00,  2.91it/s]

['village_id', 'dc_score_none_none', 'dc_score_none_size', 'dc_score_none_size_intensity', 'dc_score_none_intensity', 'dc_score_log_none', 'dc_score_log_size', 'dc_score_log_size_intensity', 'dc_score_log_intensity', 'dc_score_sqrt_none', 'dc_score_sqrt_size', 'dc_score_sqrt_size_intensity', 'dc_score_sqrt_intensity']
(345511, 1)
(345511, 13)
            dc_score_none_none  ...  dc_score_sqrt_intensity
village_id                      ...                         
628551.0              0.086022  ...                 1.136135
628556.0              0.106297  ...                 1.262953
628553.0              0.079333  ...                 1.091071
628554.0              0.104163  ...                 1.250210
628632.0              0.084576  ...                 1.126547
...                        ...  ...                      ...
209407.0              0.067198  ...                 1.158504
209403.0              0.066986  ...                 1.192917
209411.0              0.070286  ...          

In [ ]:
result_comb_df

dc_score_none_none  ...  dc_score_sqrt_intensity
village_id                      ...                         
628551.0              0.086022  ...                 1.136135
628556.0              0.106297  ...                 1.262953
628553.0              0.079333  ...                 1.091071
628554.0              0.104163  ...                 1.250210
628632.0              0.084576  ...                 1.126547
...                        ...  ...                      ...
209407.0              0.067198  ...                 1.158504
209403.0              0.066986  ...                 1.192917
209411.0              0.070286  ...                 1.198183
209412.0              0.076348  ...                 1.217780
209417.0              0.082026  ...                 1.234357

[345511 rows x 12 columns]

#### Only 

In [ ]:

scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['size', 'size_intensity', 'intensity']

result_comb_2 = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

      ids = np.argmax(res, axis=0)
      
      if ws == 'size':
        res = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'size_intensity':
        res = np.tile((area_arr*intensity_arr).reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'intensity':
        res = np.tile(intensity_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]

      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      result_comb_2[j,start:end] = res  
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}_only'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res_2 = np.append(vill_ids_arr, result_comb_2.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df_2 = pd.DataFrame(final_res_2, columns=columns)
result_comb_df_2 = result_comb_df_2.set_index('village_id')
print(result_comb_df_2)

100%|██████████| 346/346 [02:09<00:00,  2.67it/s]

['village_id', 'dc_score_none_size_only', 'dc_score_none_size_intensity_only', 'dc_score_none_intensity_only', 'dc_score_log_size_only', 'dc_score_log_size_intensity_only', 'dc_score_log_intensity_only', 'dc_score_sqrt_size_only', 'dc_score_sqrt_size_intensity_only', 'dc_score_sqrt_intensity_only']
(345511, 1)
(345511, 13)
            dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0                 151.028799  ...                      3.873700
628556.0                 151.028799  ...                      3.873700
628553.0                 151.028799  ...                      3.873700
628554.0                 151.028799  ...                      3.873700
628632.0                 151.028799  ...                      3.873700
...                             ...  ...                           ...
209407.0                  46.808138  ...                      5.682869
209403.0                  46.808138 

In [ ]:
result_comb_df_2

dc_score_none_size_only  ...  dc_score_sqrt_intensity_only
village_id                           ...                              
628551.0                 151.028799  ...                      3.873700
628556.0                 151.028799  ...                      3.873700
628553.0                 151.028799  ...                      3.873700
628554.0                 151.028799  ...                      3.873700
628632.0                 151.028799  ...                      3.873700
...                             ...  ...                           ...
209407.0                  46.808138  ...                      5.682869
209403.0                  46.808138  ...                      5.682869
209411.0                  46.808138  ...                      5.682869
209412.0                  46.808138  ...                      5.682869
209417.0                  46.808138  ...                      5.682869

[345511 rows x 9 columns]

#### Combine the two

In [ ]:
result_comb_df_final = pd.merge(result_comb_df, result_comb_df_2, left_index=True, right_index=True, how='inner')

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.086022  ...                      3.873700
628556.0              0.106297  ...                      3.873700
628553.0              0.079333  ...                      3.873700
628554.0              0.104163  ...                      3.873700
628632.0              0.084576  ...                      3.873700
...                        ...  ...                           ...
209407.0              0.067198  ...                      5.682869
209403.0              0.066986  ...                      5.682869
209411.0              0.070286  ...                      5.682869
209412.0              0.076348  ...                      5.682869
209417.0              0.082026  ...                      5.682869

[345511 rows x 21 columns]

#### Test Code

In [ ]:
res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

In [ ]:
res.shape

(2690, 1000)

In [ ]:
res_temp = np.max(res,axis=0)

In [ ]:
ids = np.argmax(res,axis=0)

In [ ]:
ids.shape

(1000,)

In [ ]:
ids

array([1453, 1455,  922, 1458,  922, 1459, 2351,  922, 2350, 2351, 1455,
       2527, 1459, 2351, 2527, 1459, 1455,  932, 2351, 2527, 1459, 2354,
       1453, 2527, 1455, 1455, 1458,  932, 1458, 2205, 1455, 2205, 2527,
       1455, 1459, 2205,  922, 2354, 1455,  932, 2354, 2350,  932, 2527,
       2527, 2205, 1459,  922, 2527, 1455, 1459, 1459,  922, 1455,  932,
       1455, 2350, 2350, 1455, 2527, 1459, 2527, 1455, 2351, 2354, 2527,
       1455, 2354, 2354, 2350, 2350, 2351,  922, 2351, 1459, 1455, 1455,
       1455, 2205, 2354, 2205, 1852, 2351, 2352, 1455, 1459, 2527, 2354,
       1455, 1455, 2351, 2350, 2351, 2354, 2354, 2527, 2205, 2205, 1455,
        922, 1455,  932, 1455, 2351, 1453, 2350, 2354, 1852, 2354,  922,
       1453, 1455, 2351, 2351, 2350, 2205, 2354,  932, 2527, 1852, 1455,
       2350, 2351, 1455, 1455, 2205, 2205, 1852, 2205, 2527, 1459,  932,
       1455, 2527, 2527, 2351, 2351, 1455, 1852,  922, 2527, 2351, 2527,
       1455, 2205, 2351, 2527, 2354,  932, 2354,  9

In [ ]:
area_arr.reshape(-1,1).shape

(2690, 1)

In [ ]:
temp = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))

In [ ]:
temp.shape

(2690, 1000)

In [ ]:
temp[[1,2],2]

array([1.88317373, 1.88390845])

In [ ]:
np.tile(np.array([0.1,0.2,0.3,0.5,0.6]).reshape(-1,1),(1,4))[[3,0],np.arange(2)]

array([0.5, 0.1])

In [ ]:
area_arr.shape

(2690,)

In [ ]:
distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled).shape

(2690, 1000)

In [ ]:
print(vill_lat_arr.shape)

(1000,)


#### Results

In [ ]:
result_comb_df_final

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.086022  ...                      3.873700
628556.0              0.106297  ...                      3.873700
628553.0              0.079333  ...                      3.873700
628554.0              0.104163  ...                      3.873700
628632.0              0.084576  ...                      3.873700
...                        ...  ...                           ...
209407.0              0.067198  ...                      5.682869
209403.0              0.066986  ...                      5.682869
209411.0              0.070286  ...                      5.682869
209412.0              0.076348  ...                      5.682869
209417.0              0.082026  ...                      5.682869

[345511 rows x 21 columns]

In [ ]:
#pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_viirs_2012.pickle','wb'))

#pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_viirs_2013.pickle','wb'))


pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_extended_time_series_viirs_2011.pickle','wb'))

In [ ]:
extended_time_series_viirs_2011 = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_extended_time_series_viirs_2011.pickle','rb'))

In [ ]:
extended_time_series_viirs_2011

dc_score_none_none  ...  dc_score_sqrt_intensity_only
village_id                      ...                              
628551.0              0.086022  ...                      3.873700
628556.0              0.106297  ...                      3.873700
628553.0              0.079333  ...                      3.873700
628554.0              0.104163  ...                      3.873700
628632.0              0.084576  ...                      3.873700
...                        ...  ...                           ...
209407.0              0.067198  ...                      5.682869
209403.0              0.066986  ...                      5.682869
209411.0              0.070286  ...                      5.682869
209412.0              0.076348  ...                      5.682869
209417.0              0.082026  ...                      5.682869

[345511 rows x 21 columns]

##(Viirs_extended_time_series) Distance from District Centre for Hypothesis_test for every year 2001,2011,2019


### 2011

#### Prepare Data

In [ ]:
dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2011.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong.pickle', 'rb'))


In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)


In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 75.77239515143489 Y: 31.21046736618144
 Intensity: 14.390136419900783
{'geometry': {'coordinates': [[[78.62504524256113, 18.83767151957523], [78.63402839540228, 18.83767151957523], [78.63402839540228, 18.846654672416427], [78.62504524256113, 18.846654672416427], [78.62504524256113, 18.83767151957523]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '2115', 'properties': {'mean': 7.3456878662109375, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :0.9413904129336101
Area2 :0.9464118524042785
POLYGON ((78.62504524256113 18.83767151957523, 78.63402839540228 18.83767151957523, 78.63402839540228 18.846654672416427, 78.62504524256113 18.846654672416427, 78.62504524256113 18.83767151957523))
shapely Method POINT (78.6295368189817 18.842163095995833)
Centroid X: 78.62863850369759 Y: 18.841264780711708
 Intensity: 7.3456878662109375
{'geometry': {'coordinates': [[[78.71487677097306, 18.810722061051642], [78.72385992381427, 18.810

In [ ]:
len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(2829, 2829, 2829)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.0188665390014648, 0.8264619363154188)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(114.45814743041993, 724.1482295977323)

#### generate_data_frame

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 






result_comb = np.zeros((1, len(vill_cen)))
j = 0


for i in tqdm(range(0, len(vill_cen_arr), 1000)):
  start, end = i, min(i+1000, len(vill_cen_arr))
  vill_cen_part = vill_cen_arr[start:end, :]

  vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
  blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

  vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
  blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

  res = distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

  res = np.min(res, axis=0)
  result_comb[j,start:end] = res
    
j += 1


columns = ['village_id']
columns += ['distance_district_centre_2011']

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.04697186 34.12209775]


100%|██████████| 346/346 [01:45<00:00,  3.27it/s]


['village_id', 'distance_district_centre_2011']
(345511, 1)
(345511, 2)
            distance_district_centre_2011
village_id                               
628551.0                        11.624978
628556.0                         9.407566
628553.0                        12.605098
628554.0                         9.600332
628632.0                        11.823704
...                                   ...
209407.0                        14.881478
209403.0                        14.928467
209411.0                        14.227684
209412.0                        13.097852
209417.0                        12.191228

[345511 rows x 1 columns]


In [ ]:
result_comb_df

distance_district_centre_2011
village_id                               
628551.0                        11.624978
628556.0                         9.407566
628553.0                        12.605098
628554.0                         9.600332
628632.0                        11.823704
...                                   ...
209407.0                        14.881478
209403.0                        14.928467
209411.0                        14.227684
209412.0                        13.097852
209417.0                        12.191228

[345511 rows x 1 columns]

In [ ]:
np.unique(result_comb_df['distance_district_centre_2011'].values)

array([2.15234790e-02, 2.78278868e-02, 3.10588262e-02, ...,
       1.22293109e+02, 1.23015257e+02, 1.33672831e+02])

In [ ]:
min(result_comb_df['distance_district_centre_2011'])

0.021523478988446195

In [ ]:
max(result_comb_df['distance_district_centre_2011'])

133.6728307129806

In [ ]:
dist_2011 = result_comb_df.copy()

### 2001

#### Prepare Data

In [ ]:
dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2001.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong.pickle', 'rb'))


In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)


In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 95.33860942873397 Y: 27.365133515305196
 Intensity: 7.593870162963867
{'geometry': {'coordinates': [[[95.3606589857078, 27.25488573043598], [95.36964213854901, 27.25488573043598], [95.36964213854901, 27.272852036118373], [95.35167583286659, 27.272852036118373], [95.35167583286659, 27.263868883277176], [95.3606589857078, 27.263868883277176], [95.3606589857078, 27.25488573043598]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '1363', 'properties': {'mean': 5.519187768300374, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :2.656318100861527
Area2 :2.6666829288319303
POLYGON ((95.3606589857078 27.25488573043598, 95.36964213854901 27.25488573043598, 95.36964213854901 27.272852036118373, 95.35167583286659 27.272852036118373, 95.35167583286659 27.263868883277176, 95.3606589857078 27.263868883277176, 95.3606589857078 27.25488573043598))
shapely Method POINT (95.36215617784801 27.26536607541738)
Centroid X: 95.3606589857078 Y:

In [ ]:
len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(2077, 2077, 2077)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.098637580871582, 0.8321749088605934)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(74.14374160766602, 376.9266201152179)

#### generate_data_frame

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 






result_comb = np.zeros((1, len(vill_cen)))
j = 0


for i in tqdm(range(0, len(vill_cen_arr), 1000)):
  start, end = i, min(i+1000, len(vill_cen_arr))
  vill_cen_part = vill_cen_arr[start:end, :]

  vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
  blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

  vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
  blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

  res = distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

  res = np.min(res, axis=0)
  result_comb[j,start:end] = res
    
j += 1


columns = ['village_id']
columns += ['distance_district_centre_2001']

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.03259882 34.09106504]


100%|██████████| 346/346 [01:24<00:00,  4.11it/s]

['village_id', 'distance_district_centre_2001']
(345511, 1)
(345511, 2)
            distance_district_centre_2001
village_id                               
628551.0                        37.067648
628556.0                        34.326317
628553.0                        36.804978
628554.0                        34.533964
628632.0                        30.872730
...                                   ...
209407.0                        23.820642
209403.0                        22.447660
209411.0                        22.273067
209412.0                        21.597649
209417.0                        21.055180

[345511 rows x 1 columns]


In [ ]:
result_comb_df

distance_district_centre_2001
village_id                               
628551.0                        37.067648
628556.0                        34.326317
628553.0                        36.804978
628554.0                        34.533964
628632.0                        30.872730
...                                   ...
209407.0                        23.820642
209403.0                        22.447660
209411.0                        22.273067
209412.0                        21.597649
209417.0                        21.055180

[345511 rows x 1 columns]

In [ ]:
np.unique(result_comb_df['distance_district_centre_2001'].values)

array([3.05978138e-02, 7.70528077e-02, 7.92855126e-02, ...,
       1.22247699e+02, 1.23630392e+02, 1.32769364e+02])

In [ ]:
min(result_comb_df['distance_district_centre_2001'])

0.03059781383900578

In [ ]:
max(result_comb_df['distance_district_centre_2001'])

132.76936401223915

In [ ]:
dist_2001 = result_comb_df.copy()

### 2019

#### Prepare Data

In [ ]:
dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2019.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong.pickle', 'rb'))


In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)


In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 79.85027234554931 Y: 26.354693052025908
 Intensity: 6.099999904632568
{'geometry': {'coordinates': [[[79.89159484861878, 26.476863930666163], [79.91854430714241, 26.476863930666163], [79.91854430714241, 26.48584708350736], [79.9095611543012, 26.48584708350736], [79.9095611543012, 26.494830236348555], [79.89159484861878, 26.494830236348555], [79.89159484861878, 26.476863930666163]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '7247', 'properties': {'mean': 5.393500089645386, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :4.457075058528114
Area2 :4.475257702270763
POLYGON ((79.89159484861878 26.476863930666163, 79.91854430714241 26.476863930666163, 79.91854430714241 26.48584708350736, 79.9095611543012 26.48584708350736, 79.9095611543012 26.494830236348555, 79.89159484861878 26.494830236348555, 79.89159484861878 26.476863930666163))
shapely Method POINT (79.90327294731236 26.48494876822324)
Centroid X: 79.9044279241062

In [ ]:
len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(7961, 7961, 7961)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.033750057220459, 0.8207103399652012)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(270.75, 1461.9729126409825)

#### generate_data_frame

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 






result_comb = np.zeros((1, len(vill_cen)))
j = 0


for i in tqdm(range(0, len(vill_cen_arr), 1000)):
  start, end = i, min(i+1000, len(vill_cen_arr))
  vill_cen_part = vill_cen_arr[start:end, :]

  vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
  blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

  vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
  blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

  res = distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

  res = np.min(res, axis=0)
  result_comb[j,start:end] = res
    
j += 1


columns = ['village_id']
columns += ['distance_district_centre_2019']

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





345511 345511
[88.24738141 32.46384974]
[96.16265126 34.64614312]


100%|██████████| 346/346 [05:48<00:00,  1.01s/it]

['village_id', 'distance_district_centre_2019']
(345511, 1)
(345511, 2)
            distance_district_centre_2019
village_id                               
628551.0                         5.820180
628556.0                         9.512279
628553.0                         3.748125
628554.0                         6.980162
628632.0                        12.328731
...                                   ...
209407.0                        14.176115
209403.0                        14.237579
209411.0                        13.539339
209412.0                        12.422336
209417.0                        11.531312

[345511 rows x 1 columns]


In [ ]:
result_comb_df

distance_district_centre_2019
village_id                               
628551.0                         5.820180
628556.0                         9.512279
628553.0                         3.748125
628554.0                         6.980162
628632.0                        12.328731
...                                   ...
209407.0                        14.176115
209403.0                        14.237579
209411.0                        13.539339
209412.0                        12.422336
209417.0                        11.531312

[345511 rows x 1 columns]

In [ ]:
np.unique(result_comb_df['distance_district_centre_2019'].values)

array([8.77139887e-03, 2.72926891e-02, 2.80080310e-02, ...,
       1.05572592e+02, 1.06780642e+02, 1.10767383e+02])

In [ ]:
min(result_comb_df['distance_district_centre_2019'])

0.008771398873085945

In [ ]:
max(result_comb_df['distance_district_centre_2019'])

110.767383343352

In [ ]:
dist_2019 = result_comb_df.copy()

### Combine dataFrame

In [ ]:
distance_data = dist_2011.copy()

In [ ]:
distance_data = distance_data.merge(dist_2001,how='inner',left_index=True,right_index=True)

In [ ]:
distance_data

distance_district_centre_2011  distance_district_centre_2001
village_id                                                              
628551.0                        11.624978                      37.067648
628556.0                         9.407566                      34.326317
628553.0                        12.605098                      36.804978
628554.0                         9.600332                      34.533964
628632.0                        11.823704                      30.872730
...                                   ...                            ...
209407.0                        14.881478                      23.820642
209403.0                        14.928467                      22.447660
209411.0                        14.227684                      22.273067
209412.0                        13.097852                      21.597649
209417.0                        12.191228                      21.055180

[345511 rows x 2 columns]

In [ ]:
distance_data = distance_data.merge(dist_2019,how='inner',left_index=True,right_index=True)

In [ ]:
distance_data

distance_district_centre_2011  distance_district_centre_2001  \
village_id                                                                 
628551.0                        11.624978                      37.067648   
628556.0                         9.407566                      34.326317   
628553.0                        12.605098                      36.804978   
628554.0                         9.600332                      34.533964   
628632.0                        11.823704                      30.872730   
...                                   ...                            ...   
209407.0                        14.881478                      23.820642   
209403.0                        14.928467                      22.447660   
209411.0                        14.227684                      22.273067   
209412.0                        13.097852                      21.597649   
209417.0                        12.191228                      21.055180   

            distance_district_centre_2019  
village_id                                 
628551.0                         5.820180  
628556.0                         9.512279  
628553.0                         3.748125  
628554.0                         6.980162  
628632.0                        12.328731  
...                                   ...  
209407.0                        14.176115  
209403.0                        14.237579  
209411.0                        13.539339  
209412.0                        12.422336  
209417.0                        11.531312  

[345511 rows x 3 columns]

In [ ]:
df_village = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/Latest_script_Data_for_hyothesis_testing_March_02_2022/final_combined_without_temporal_correction_arch2_predicted_ADI_for_2001_2019_ground_truth_ADI_2011_variables_predicted_from_arch2_pop_sc_st_lit_village_data.pkl','rb'))

In [ ]:
df_village

2001_cc_code VILL_CODE_2001 DIST_CODE_2001  \
index_col_village_code_2011                                                   
27378                         301000100000500       00000500              1   
27379                         301000100000600       00000600              1   
27380                         301000100000700       00000700              1   
27381                         301000100000800       00000800              1   
27382                         301000100000900       00000900              1   
...                                       ...            ...            ...   
644661                       3310000700779700       00779700             10   
644682                       3310000700781800       00781800             10   
644683                       3310000700781900       00781900             10   
644687                       3310000700782300       00782300             10   
644693                       3310000700782900       00782900             10   

                            STATE_CODE_2001 VILL_CODE_2011 DIST_CODE_2011  \
index_col_village_code_2011                                                 
27378                                     3          27378             35   
27379                                     3          27379             35   
27380                                     3          27380             35   
27381                                     3          27381             35   
27382                                     3          27382             35   
...                                     ...            ...            ...   
644661                                   33         644661            633   
644682                                   33         644682            633   
644683                                   33         644683            633   
644687                                   33         644687            633   
644693                                   33         644693            633   

                            STATE_CODE_2011  distance_district_centre  \
index_col_village_code_2011                                             
27378                                     3                  6.111495   
27379                                     3                  4.878376   
27380                                     3                  9.103092   
27381                                     3                  6.777262   
27382                                     3                  6.786058   
...                                     ...                       ...   
644661                                   33                  2.643310   
644682                                   33                  2.493440   
644683                                   33                  3.325585   
644687                                   33                  5.413251   
644693                                   33                  9.476738   

                             dc_score_none_none_old  inverted_dist  ...  \
index_col_village_code_2011                                         ...   
27378                                      0.407427       0.163626  ...   
27379                                      0.658831       0.204986  ...   
27380                                      0.080571       0.109853  ...   
27381                                      0.309724       0.147552  ...   
27382                                      0.308561       0.147361  ...   
...                                             ...            ...  ...   
644661                                     1.712385       0.378314  ...   
644682                                     1.850601       0.401052  ...   
644683                                     1.240612       0.300699  ...   
644687                                     0.535717       0.184732  ...   
644693                                     0.054244       0.105522  ...   

                             FC_2011  ASSET_2011  LIT_2011  MSW_2011  BF_2019

In [ ]:
df_village_new = df_village.merge(distance_data,how='inner',left_index=True,right_index=True).set_index(df_village.index)

In [ ]:
df_village_new

2001_cc_code VILL_CODE_2001 DIST_CODE_2001  \
index_col_village_code_2011                                                   
27378                         301000100000500       00000500              1   
27379                         301000100000600       00000600              1   
27380                         301000100000700       00000700              1   
27381                         301000100000800       00000800              1   
27382                         301000100000900       00000900              1   
...                                       ...            ...            ...   
644661                       3310000700779700       00779700             10   
644682                       3310000700781800       00781800             10   
644683                       3310000700781900       00781900             10   
644687                       3310000700782300       00782300             10   
644693                       3310000700782900       00782900             10   

                            STATE_CODE_2001 VILL_CODE_2011 DIST_CODE_2011  \
index_col_village_code_2011                                                 
27378                                     3          27378             35   
27379                                     3          27379             35   
27380                                     3          27380             35   
27381                                     3          27381             35   
27382                                     3          27382             35   
...                                     ...            ...            ...   
644661                                   33         644661            633   
644682                                   33         644682            633   
644683                                   33         644683            633   
644687                                   33         644687            633   
644693                                   33         644693            633   

                            STATE_CODE_2011  distance_district_centre  \
index_col_village_code_2011                                             
27378                                     3                  6.111495   
27379                                     3                  4.878376   
27380                                     3                  9.103092   
27381                                     3                  6.777262   
27382                                     3                  6.786058   
...                                     ...                       ...   
644661                                   33                  2.643310   
644682                                   33                  2.493440   
644683                                   33                  3.325585   
644687                                   33                  5.413251   
644693                                   33                  9.476738   

                             dc_score_none_none_old  inverted_dist  ...  \
index_col_village_code_2011                                         ...   
27378                                      0.407427       0.163626  ...   
27379                                      0.658831       0.204986  ...   
27380                                      0.080571       0.109853  ...   
27381                                      0.309724       0.147552  ...   
27382                                      0.308561       0.147361  ...   
...                                             ...            ...  ...   
644661                                     1.712385       0.378314  ...   
644682                                     1.850601       0.401052  ...   
644683                                     1.240612       0.300699  ...   
644687                                     0.535717       0.184732  ...   
644693                                     0.054244       0.105522  ...   

                             MSW_2011  BF_2019  FC_2019  MSW_2019  ASSET_2019

In [ ]:
vill_cen

{628551: [80.05962435116712, 13.501958309972064],
 628556: [80.12231434564274, 13.493918048407249],
 628553: [80.02070780159008, 13.481903326001023],
 628554: [80.05087582613181, 13.473695697682952],
 628632: [80.20263708887512, 13.467829806711366],
 628631: [80.1919186023265, 13.46895217942312],
 628565: [80.11427852571413, 13.4592917423097],
 628640: [80.22087939307657, 13.459198968633396],
 628644: [80.18218896512323, 13.458771459611821],
 628643: [80.19526236426327, 13.455093246499034],
 628564: [80.13317320339995, 13.452531001268559],
 628641: [80.21429444570371, 13.451044808556833],
 628568: [80.04175155421969, 13.439876394237384],
 628642: [80.1995057594074, 13.445074131992401],
 628584: [80.11105083308831, 13.443875937938024],
 628650: [80.23111104290578, 13.431007015438526],
 628645: [80.17977997441044, 13.444061803217688],
 628587: [80.1609915599856, 13.43972861997042],
 628646: [80.20594407834771, 13.436114775494564],
 628586: [80.15171579380846, 13.419679060074225],
 628651

In [ ]:
pickle.dump(df_village_new, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/Latest_script_Data_for_hyothesis_testing_March_02_2022/final_combined_without_temporal_correction_arch2_predicted_ADI_for_2001_2019_ground_truth_ADI_2011_variables_predicted_from_arch2_pop_sc_st_lit_village_data.pkl','wb'))

In [ ]:
df_village_2 = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/Latest_script_Data_for_hyothesis_testing_March_02_2022/final_combined_without_temporal_correction_arch2_predicted_ADI_for_2001_2019_ground_truth_ADI_2011_variables_predicted_from_arch2_pop_sc_st_lit_village_data.pkl','rb'))

In [ ]:
df_village_2

2001_cc_code VILL_CODE_2001 DIST_CODE_2001  \
index_col_village_code_2011                                                   
27378                         301000100000500       00000500              1   
27379                         301000100000600       00000600              1   
27380                         301000100000700       00000700              1   
27381                         301000100000800       00000800              1   
27382                         301000100000900       00000900              1   
...                                       ...            ...            ...   
644661                       3310000700779700       00779700             10   
644682                       3310000700781800       00781800             10   
644683                       3310000700781900       00781900             10   
644687                       3310000700782300       00782300             10   
644693                       3310000700782900       00782900             10   

                            STATE_CODE_2001 VILL_CODE_2011 DIST_CODE_2011  \
index_col_village_code_2011                                                 
27378                                     3          27378             35   
27379                                     3          27379             35   
27380                                     3          27380             35   
27381                                     3          27381             35   
27382                                     3          27382             35   
...                                     ...            ...            ...   
644661                                   33         644661            633   
644682                                   33         644682            633   
644683                                   33         644683            633   
644687                                   33         644687            633   
644693                                   33         644693            633   

                            STATE_CODE_2011  distance_district_centre  \
index_col_village_code_2011                                             
27378                                     3                  6.111495   
27379                                     3                  4.878376   
27380                                     3                  9.103092   
27381                                     3                  6.777262   
27382                                     3                  6.786058   
...                                     ...                       ...   
644661                                   33                  2.643310   
644682                                   33                  2.493440   
644683                                   33                  3.325585   
644687                                   33                  5.413251   
644693                                   33                  9.476738   

                             dc_score_none_none_old  inverted_dist  ...  \
index_col_village_code_2011                                         ...   
27378                                      0.407427       0.163626  ...   
27379                                      0.658831       0.204986  ...   
27380                                      0.080571       0.109853  ...   
27381                                      0.309724       0.147552  ...   
27382                                      0.308561       0.147361  ...   
...                                             ...            ...  ...   
644661                                     1.712385       0.378314  ...   
644682                                     1.850601       0.401052  ...   
644683                                     1.240612       0.300699  ...   
644687                                     0.535717       0.184732  ...   
644693                                     0.054244       0.105522  ...   

                             MSW_2011  BF_2019  FC_2019  MSW_2019  ASSET_2019

## Generate for WB : Viirs_extended_time_series

In [ ]:
#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_viirs_updated_2012.geojson'


#dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_viirs_updated_2013.geojson'


dir = '/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/geoJson/NightLight_District_Blobs_extended_time_series_viirs_2011.geojson'

f = open(os.path.join(dir), 'r')
jsonstring = f.read()
data = json.loads(jsonstring)

In [ ]:
#vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong.pickle', 'rb'))


vill_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/vill_geoinfo_latlong_with_WB.pickle', 'rb'))

blob_cen = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_centroids.pickle','rb'))
blob_intensities = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_intensities.pickle','rb'))
blob_areas = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/2.Distance_from_Nearest_District_Centres/blob_areas.pickle','rb'))

In [ ]:
len(data['features'])

2829

In [ ]:
min(blob_areas)

0.9977632945385269

In [ ]:
blob_intensities[0]

6.170222759246826

In [ ]:
from area import area

def calulateArea(geo):
  poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
  # pa = pyproj.Proj("+proj=aea") # not work anymore.
  w,s,e,n = poly.bounds
  pa = pyproj.Proj(proj='aea', lat_1 = s, lat_2 = n)
  #Extract the outer ring of the polygon
  x, y = poly.exterior.coords.xy
  #projection
  x, y = pa(list(x[:-1]), list(y[:-1]))
  #create a new geojson of the new projection polygon
  cop = {"type": "Polygon", "coordinates": [zip(x, y)]}
  #geojson -> shapely polygon, 
  #then use the polygon's predefined function to calculate area.
  area1 = shape(cop).area / 1000000 #km^2
  print("Area1 :"+str(area1))

  area2 = area(geo)
  print("Area2 :"+str(area2 / 1000000))

  return area1




from shapely import wkt


def getCentroid1(geo):
   poly = Polygon([tuple(l) for l in geo['coordinates'][0]])
   print(str(poly))
   p1 = wkt.loads(str(poly))

   print("shapely Method "+p1.centroid.wkt)

def getCentroid2(geo):
     vertexes = geo['coordinates'][0]
     _x_list = [vertex [0] for vertex in vertexes]
     _y_list = [vertex [1] for vertex in vertexes]
     _len = len(vertexes)
     _x = sum(_x_list) / _len
     _y = sum(_y_list) / _len
     print("Centroid X: "+str(_x)+" Y: "+str(_y))
     return(_x, _y)




In [ ]:
blobPolygonList = []
blobAreaList = []
blobIntensityList = []
blobCentroidList = []


for feature in data['features']:
  print(feature)
  blobAreaList.append(calulateArea(feature['geometry']))
  getCentroid1(feature['geometry'])
  blobCentroidList.append(getCentroid2(feature['geometry']))
  print(" Intensity: "+str(feature['properties']['mean']))
  blobIntensityList.append(feature['properties']['mean'])

  #break

Streaming output truncated to the last 5000 lines.
Centroid X: 75.77239515143489 Y: 31.21046736618144
 Intensity: 14.390136419900783
{'geometry': {'coordinates': [[[78.62504524256113, 18.83767151957523], [78.63402839540228, 18.83767151957523], [78.63402839540228, 18.846654672416427], [78.62504524256113, 18.846654672416427], [78.62504524256113, 18.83767151957523]]], 'geodesic': False, 'type': 'Polygon'}, 'id': '2115', 'properties': {'mean': 7.3456878662109375, 'nighlight_intensity': 1}, 'type': 'Feature'}
Area1 :0.9413904129336101
Area2 :0.9464118524042785
POLYGON ((78.62504524256113 18.83767151957523, 78.63402839540228 18.83767151957523, 78.63402839540228 18.846654672416427, 78.62504524256113 18.846654672416427, 78.62504524256113 18.83767151957523))
shapely Method POINT (78.6295368189817 18.842163095995833)
Centroid X: 78.62863850369759 Y: 18.841264780711708
 Intensity: 7.3456878662109375
{'geometry': {'coordinates': [[[78.71487677097306, 18.810722061051642], [78.72385992381427, 18.810

In [ ]:


len(blobAreaList) , len(blobIntensityList) , len(blobCentroidList)

(2829, 2829, 2829)

In [ ]:
min(blobIntensityList) , min(blobAreaList)

(1.0188665390014648, 0.8264619363154188)

In [ ]:
max(blobIntensityList) , max(blobAreaList)

(114.45814743041993, 724.1482295977323)

#### Without Only

In [ ]:
result = np.zeros(len(vill_cen))

vill_ids,vill_centroids = list(vill_cen.keys()), list(vill_cen.values())
# print(vill_centroids[1000:1010])
print(len(vill_ids), len(vill_centroids))



vill_cen_arr = np.array(vill_centroids)
print(np.max(vill_cen_arr, axis=0))


blob_cen_arr = np.array(blobCentroidList)
print(np.max(blob_cen_arr, axis=0))


area_arr = np.array(blobAreaList)

intensity_arr = np.array(blobIntensityList)


def distance(lat1, lat2, lon1, lon2): 
  # Haversine formula
  # The math module contains a function named 
  # radians which converts from degrees to radians. 
  lon1 = np.radians(lon1)
  lon2 = np.radians(lon2) 
  lat1 = np.radians(lat1) 
  lat2 = np.radians(lat2) 

  # Haversine formula 
  dlon = lon2 - lon1 
  dlat = lat2 - lat1 
  a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2

  c = 2 * np.arcsin(np.sqrt(a))

  # Radius of earth in kilometers. Use 3956 for miles 
  r = 6371

  # calculate the result 
  return(c * r) 




scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['none','size', 'size_intensity', 'intensity']

result_comb = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

    
      
      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      res = np.max(res, axis=0)
      result_comb[j,start:end] = res
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res = np.append(vill_ids_arr, result_comb.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df = pd.DataFrame(final_res, columns=columns)
result_comb_df = result_comb_df.set_index('village_id')
print(result_comb_df)





522205 522205
[1385127.01891347 3029260.46992541]
[96.04697186 34.12209775]


100%|██████████| 523/523 [02:31<00:00,  3.45it/s]

['village_id', 'dc_score_none_none', 'dc_score_none_size', 'dc_score_none_size_intensity', 'dc_score_none_intensity', 'dc_score_log_none', 'dc_score_log_size', 'dc_score_log_size_intensity', 'dc_score_log_intensity', 'dc_score_sqrt_none', 'dc_score_sqrt_size', 'dc_score_sqrt_size_intensity', 'dc_score_sqrt_intensity']
(522205, 1)
(522205, 13)
            dc_score_none_none  dc_score_none_size  \
village_id                                           
60683.0               0.054712            3.414007   
58270.0               0.086446            3.613324   
58278.0               0.065222            3.660551   
58297.0               0.071271            3.627885   
58269.0               0.088143            3.657437   
...                        ...                 ...   
335320.0              0.000319            0.145047   
335170.0              0.000087            0.052211   
335315.0              0.000489            0.200894   
318467.0              0.000120            0.071607   
318465.

In [ ]:
result_comb_df

dc_score_none_none  dc_score_none_size  \
village_id                                           
60683.0               0.054712            3.414007   
58270.0               0.086446            3.613324   
58278.0               0.065222            3.660551   
58297.0               0.071271            3.627885   
58269.0               0.088143            3.657437   
...                        ...                 ...   
335320.0              0.000319            0.145047   
335170.0              0.000087            0.052211   
335315.0              0.000489            0.200894   
318467.0              0.000120            0.071607   
318465.0              0.000102            0.060028   

            dc_score_none_size_intensity  dc_score_none_intensity  \
village_id                                                          
60683.0                       174.092005                 1.349222   
58270.0                       184.255885                 0.767768   
58278.0                       186.664125                 0.699896   
58297.0                       184.998387                 0.606656   
58269.0                       186.505368                 0.923385   
...                                  ...                      ...   
335320.0                        7.396460                 0.022056   
335170.0                        2.662398                 0.008577   
335315.0                       10.796235                 0.034234   
318467.0                        3.651472                 0.010622   
318465.0                        3.061057                 0.010201   

            dc_score_log_none  dc_score_log_size  dc_score_log_size_intensity  \
village_id                                                                      
60683.0             -2.905664           1.227887                     5.159584   
58270.0             -2.448230           1.284628                     5.216325   
58278.0             -2.729963           1.297614                     5.229311   
58297.0             -2.641268           1.288650                     5.220347   
58269.0             -2.428800           1.296763                     5.228460   
...                       ...                ...                          ...   
335320.0            -8.051204          -1.930696                     2.001002   
335170.0            -9.345976          -2.952470                     0.979227   
335315.0            -7.623550          -1.604978                     2.379197   
318467.0            -9.026517          -2.636567                     1.295130   
318465.0            -9.188718          -2.812937                     1.118760   

            dc_score_log_intensity  dc_score_sqrt_none  dc_score_sqrt_size  \
village_id                                                                   
60683.0                   0.299528            0.233907            1.847703   
58270.0                  -0.264268            0.294018            1.900875   
58278.0                  -0.356824            0.255385            1.913257   
58297.0                  -0.499793            0.266966            1.904701   
58269.0                  -0.079709            0.296888            1.912443   
...                            ...                 ...                 ...   
335320.0                 -3.814154            0.017853            0.380851   
335170.0                 -4.758670            0.009344            0.228496   
335315.0                 -3.374540            0.022109            0.448212   
318467.0                 -4.544860            0.010963            0.267594   
318465.0                 -4.585255            0.010109            0.245007   

            dc_score_sqrt_size_intensity  dc_score_sqrt_intensity  
village_id                                                         
60683.0                        13.194393                 1.161560  
58270.0                        13.574089                 0.876223  
58278.0                        13.662508                 0.836598  
58

#### Only 

In [ ]:

scaling_scheme = ['none', 'log', 'sqrt']
# weighting_scheme = ['none', 'size', 'size_intensity']
# weighting_scheme = ['intensity']
weighting_scheme = ['size', 'size_intensity', 'intensity']

result_comb_2 = np.zeros((len(scaling_scheme)*len(weighting_scheme), len(vill_cen)))
j = 0


for ss in scaling_scheme:
  for ws in weighting_scheme:
    for i in tqdm(range(0, len(vill_cen_arr), 1000)):
      start, end = i, min(i+1000, len(vill_cen_arr))
      vill_cen_part = vill_cen_arr[start:end, :]

      vill_lat_arr, vill_lon_arr = vill_cen_part[:,1], vill_cen_part[:,0]
      blob_lat_arr, blob_lon_arr = blob_cen_arr[:,1], blob_cen_arr[:,0]

      vill_lat_tiled, vill_lon_tiled = np.tile(vill_lat_arr, (len(blob_lat_arr),1)), np.tile(vill_lon_arr, (len(blob_lon_arr),1))
      blob_lat_tiled, blob_lon_tiled = np.tile(blob_lat_arr, (len(vill_lat_arr),1)).T, np.tile(blob_lon_arr, (len(vill_lon_arr),1)).T

      res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

      if ws == 'size':
        res *= area_arr.reshape(-1,1)
      elif ws == 'size_intensity':
        res *= intensity_arr.reshape(-1,1)*area_arr.reshape(-1,1)
      elif ws == 'intensity':
        res *= intensity_arr.reshape(-1,1)

      ids = np.argmax(res, axis=0)
      
      if ws == 'size':
        res = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'size_intensity':
        res = np.tile((area_arr*intensity_arr).reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]
      elif ws == 'intensity':
        res = np.tile(intensity_arr.reshape(-1,1), (1, len(vill_cen_part)))[ids, np.arange(len(vill_cen_part))]

      if ss == 'log':
        res = np.log(res)
      elif ss == 'sqrt':
        res = np.sqrt(res)

      result_comb_2[j,start:end] = res  
    
    j += 1


columns = ['village_id']
for sc1 in scaling_scheme:
  for sc2 in weighting_scheme:
    columns += ['dc_score_{}_{}_only'.format(sc1, sc2)]

print(columns)


vill_ids_arr = np.array(vill_ids).reshape(-1,1)
print(vill_ids_arr.shape)


final_res_2 = np.append(vill_ids_arr, result_comb_2.T, axis=1)
print(final_res.shape)



import pandas as pd
result_comb_df_2 = pd.DataFrame(final_res_2, columns=columns)
result_comb_df_2 = result_comb_df_2.set_index('village_id')
print(result_comb_df_2)

100%|██████████| 523/523 [02:36<00:00,  3.33it/s]

['village_id', 'dc_score_none_size_only', 'dc_score_none_size_intensity_only', 'dc_score_none_intensity_only', 'dc_score_log_size_only', 'dc_score_log_size_intensity_only', 'dc_score_log_intensity_only', 'dc_score_sqrt_size_only', 'dc_score_sqrt_size_intensity_only', 'dc_score_sqrt_intensity_only']
(522205, 1)
(522205, 13)
            dc_score_none_size_only  dc_score_none_size_intensity_only  \
village_id                                                               
60683.0                  724.148230                       36926.818956   
58270.0                  724.148230                       36926.818956   
58278.0                  724.148230                       36926.818956   
58297.0                  724.148230                       36926.818956   
58269.0                  724.148230                       36926.818956   
...                             ...                                ...   
335320.0                 724.148230                       36926.818956   
335170.0 

In [ ]:
result_comb_df_2

dc_score_none_size_only  dc_score_none_size_intensity_only  \
village_id                                                               
60683.0                  724.148230                       36926.818956   
58270.0                  724.148230                       36926.818956   
58278.0                  724.148230                       36926.818956   
58297.0                  724.148230                       36926.818956   
58269.0                  724.148230                       36926.818956   
...                             ...                                ...   
335320.0                 724.148230                       36926.818956   
335170.0                 724.148230                       36926.818956   
335315.0                 513.354126                       27588.147069   
318467.0                 724.148230                       36926.818956   
318465.0                 724.148230                       36926.818956   

            dc_score_none_intensity_only  dc_score_log_size_only  \
village_id                                                         
60683.0                        32.787412                6.584996   
58270.0                        24.400255                6.584996   
58278.0                        24.400255                6.584996   
58297.0                        34.754211                6.584996   
58269.0                        24.400255                6.584996   
...                                  ...                     ...   
335320.0                       91.122937                6.584996   
335170.0                      114.458147                6.584996   
335315.0                      114.458147                6.240966   
318467.0                      114.458147                6.584996   
318465.0                      114.458147                6.584996   

            dc_score_log_size_intensity_only  dc_score_log_intensity_only  \
village_id                                                                  
60683.0                            10.516693                     3.490045   
58270.0                            10.516693                     3.194594   
58278.0                            10.516693                     3.194594   
58297.0                            10.516693                     3.548301   
58269.0                            10.516693                     3.194594   
...                                      ...                          ...   
335320.0                           10.516693                     4.512210   
335170.0                           10.516693                     4.740209   
335315.0                           10.225142                     4.740209   
318467.0                           10.516693                     4.740209   
318465.0                           10.516693                     4.740209   

            dc_score_sqrt_size_only  dc_score_sqrt_size_intensity_only  \
village_id                                                               
60683.0                   26.910002                         192.163521   
58270.0                   26.910002                         192.163521   
58278.0                   26.910002                         192.163521   
58297.0                   26.910002                         192.163521   
58269.0                   26.910002                         192.163521   
...                             ...                                ...   
335320.0                  26.910002                         192.163521   
335170.0                  26.910002                         192.163521   
335315.0                  22.657319                         166.096800   
318467.0                  26.910002                         192.163521   
318465.0                  26.910002                         192.163521   

            dc_score_sqrt_intensity_only  
village_id                                
60683.0                         5.726029  
58270.0                         4.939661  
58278.0                    

#### Combine the two

In [ ]:
result_comb_df_final = pd.merge(result_comb_df, result_comb_df_2, left_index=True, right_index=True, how='inner')

In [ ]:
result_comb_df_final

dc_score_none_none  dc_score_none_size  \
village_id                                           
60683.0               0.054712            3.414007   
58270.0               0.086446            3.613324   
58278.0               0.065222            3.660551   
58297.0               0.071271            3.627885   
58269.0               0.088143            3.657437   
...                        ...                 ...   
335320.0              0.000319            0.145047   
335170.0              0.000087            0.052211   
335315.0              0.000489            0.200894   
318467.0              0.000120            0.071607   
318465.0              0.000102            0.060028   

            dc_score_none_size_intensity  dc_score_none_intensity  \
village_id                                                          
60683.0                       174.092005                 1.349222   
58270.0                       184.255885                 0.767768   
58278.0                       186.664125                 0.699896   
58297.0                       184.998387                 0.606656   
58269.0                       186.505368                 0.923385   
...                                  ...                      ...   
335320.0                        7.396460                 0.022056   
335170.0                        2.662398                 0.008577   
335315.0                       10.796235                 0.034234   
318467.0                        3.651472                 0.010622   
318465.0                        3.061057                 0.010201   

            dc_score_log_none  dc_score_log_size  dc_score_log_size_intensity  \
village_id                                                                      
60683.0             -2.905664           1.227887                     5.159584   
58270.0             -2.448230           1.284628                     5.216325   
58278.0             -2.729963           1.297614                     5.229311   
58297.0             -2.641268           1.288650                     5.220347   
58269.0             -2.428800           1.296763                     5.228460   
...                       ...                ...                          ...   
335320.0            -8.051204          -1.930696                     2.001002   
335170.0            -9.345976          -2.952470                     0.979227   
335315.0            -7.623550          -1.604978                     2.379197   
318467.0            -9.026517          -2.636567                     1.295130   
318465.0            -9.188718          -2.812937                     1.118760   

            dc_score_log_intensity  dc_score_sqrt_none  dc_score_sqrt_size  \
village_id                                                                   
60683.0                   0.299528            0.233907            1.847703   
58270.0                  -0.264268            0.294018            1.900875   
58278.0                  -0.356824            0.255385            1.913257   
58297.0                  -0.499793            0.266966            1.904701   
58269.0                  -0.079709            0.296888            1.912443   
...                            ...                 ...                 ...   
335320.0                 -3.814154            0.017853            0.380851   
335170.0                 -4.758670            0.009344            0.228496   
335315.0                 -3.374540            0.022109            0.448212   
318467.0                 -4.544860            0.010963            0.267594   
318465.0                 -4.585255            0.010109            0.245007   

            ...  dc_score_sqrt_intensity  dc_score_none_size_only  \
village_id  ...                                                     
60683.0     ...                 1.161560               724.148230   
58270.0     ...                 0.876223               724.148230   
58278.0     ...                 0.836598               724.148230 

#### Test Code

In [ ]:
res = 1/distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled)

In [ ]:
res.shape

(2690, 1000)

In [ ]:
res_temp = np.max(res,axis=0)

In [ ]:
ids = np.argmax(res,axis=0)

In [ ]:
ids.shape

(1000,)

In [ ]:
ids

array([1453, 1455,  922, 1458,  922, 1459, 2351,  922, 2350, 2351, 1455,
       2527, 1459, 2351, 2527, 1459, 1455,  932, 2351, 2527, 1459, 2354,
       1453, 2527, 1455, 1455, 1458,  932, 1458, 2205, 1455, 2205, 2527,
       1455, 1459, 2205,  922, 2354, 1455,  932, 2354, 2350,  932, 2527,
       2527, 2205, 1459,  922, 2527, 1455, 1459, 1459,  922, 1455,  932,
       1455, 2350, 2350, 1455, 2527, 1459, 2527, 1455, 2351, 2354, 2527,
       1455, 2354, 2354, 2350, 2350, 2351,  922, 2351, 1459, 1455, 1455,
       1455, 2205, 2354, 2205, 1852, 2351, 2352, 1455, 1459, 2527, 2354,
       1455, 1455, 2351, 2350, 2351, 2354, 2354, 2527, 2205, 2205, 1455,
        922, 1455,  932, 1455, 2351, 1453, 2350, 2354, 1852, 2354,  922,
       1453, 1455, 2351, 2351, 2350, 2205, 2354,  932, 2527, 1852, 1455,
       2350, 2351, 1455, 1455, 2205, 2205, 1852, 2205, 2527, 1459,  932,
       1455, 2527, 2527, 2351, 2351, 1455, 1852,  922, 2527, 2351, 2527,
       1455, 2205, 2351, 2527, 2354,  932, 2354,  9

In [ ]:
area_arr.reshape(-1,1).shape

(2690, 1)

In [ ]:
temp = np.tile(area_arr.reshape(-1,1), (1, len(vill_cen_part)))

In [ ]:
temp.shape

(2690, 1000)

In [ ]:
temp[[1,2],2]

array([1.88317373, 1.88390845])

In [ ]:
np.tile(np.array([0.1,0.2,0.3,0.5,0.6]).reshape(-1,1),(1,4))[[3,0],np.arange(2)]

array([0.5, 0.1])

In [ ]:
area_arr.shape

(2690,)

In [ ]:
distance(vill_lat_tiled, blob_lat_tiled, vill_lon_tiled, blob_lon_tiled).shape

(2690, 1000)

In [ ]:
print(vill_lat_arr.shape)

(1000,)


#### Results

In [ ]:
result_comb_df_final

dc_score_none_none  dc_score_none_size  \
village_id                                           
60683.0               0.054712            3.414007   
58270.0               0.086446            3.613324   
58278.0               0.065222            3.660551   
58297.0               0.071271            3.627885   
58269.0               0.088143            3.657437   
...                        ...                 ...   
335320.0              0.000319            0.145047   
335170.0              0.000087            0.052211   
335315.0              0.000489            0.200894   
318467.0              0.000120            0.071607   
318465.0              0.000102            0.060028   

            dc_score_none_size_intensity  dc_score_none_intensity  \
village_id                                                          
60683.0                       174.092005                 1.349222   
58270.0                       184.255885                 0.767768   
58278.0                       186.664125                 0.699896   
58297.0                       184.998387                 0.606656   
58269.0                       186.505368                 0.923385   
...                                  ...                      ...   
335320.0                        7.396460                 0.022056   
335170.0                        2.662398                 0.008577   
335315.0                       10.796235                 0.034234   
318467.0                        3.651472                 0.010622   
318465.0                        3.061057                 0.010201   

            dc_score_log_none  dc_score_log_size  dc_score_log_size_intensity  \
village_id                                                                      
60683.0             -2.905664           1.227887                     5.159584   
58270.0             -2.448230           1.284628                     5.216325   
58278.0             -2.729963           1.297614                     5.229311   
58297.0             -2.641268           1.288650                     5.220347   
58269.0             -2.428800           1.296763                     5.228460   
...                       ...                ...                          ...   
335320.0            -8.051204          -1.930696                     2.001002   
335170.0            -9.345976          -2.952470                     0.979227   
335315.0            -7.623550          -1.604978                     2.379197   
318467.0            -9.026517          -2.636567                     1.295130   
318465.0            -9.188718          -2.812937                     1.118760   

            dc_score_log_intensity  dc_score_sqrt_none  dc_score_sqrt_size  \
village_id                                                                   
60683.0                   0.299528            0.233907            1.847703   
58270.0                  -0.264268            0.294018            1.900875   
58278.0                  -0.356824            0.255385            1.913257   
58297.0                  -0.499793            0.266966            1.904701   
58269.0                  -0.079709            0.296888            1.912443   
...                            ...                 ...                 ...   
335320.0                 -3.814154            0.017853            0.380851   
335170.0                 -4.758670            0.009344            0.228496   
335315.0                 -3.374540            0.022109            0.448212   
318467.0                 -4.544860            0.010963            0.267594   
318465.0                 -4.585255            0.010109            0.245007   

            ...  dc_score_sqrt_intensity  dc_score_none_size_only  \
village_id  ...                                                     
60683.0     ...                 1.161560               724.148230   
58270.0     ...                 0.876223               724.148230   
58278.0     ...                 0.836598               724.148230 

In [ ]:
#pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_viirs_2012.pickle','wb'))

#pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_viirs_2013.pickle','wb'))


pickle.dump(result_comb_df_final, open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_extended_time_series_viirs_2011_WB.pickle','wb'))

In [ ]:
extended_time_series_viirs_2011 = pickle.load(open('/content/drive/MyDrive/Scripts_and_Data_Transfer/3.Arch_2_Procedure/3.Obtain_Nightlight_Features/computedData/result_extended_time_series_viirs_2011_WB.pickle','rb'))

In [ ]:
extended_time_series_viirs_2011

dc_score_none_none  dc_score_none_size  \
village_id                                           
60683.0               0.054712            3.414007   
58270.0               0.086446            3.613324   
58278.0               0.065222            3.660551   
58297.0               0.071271            3.627885   
58269.0               0.088143            3.657437   
...                        ...                 ...   
335320.0              0.000319            0.145047   
335170.0              0.000087            0.052211   
335315.0              0.000489            0.200894   
318467.0              0.000120            0.071607   
318465.0              0.000102            0.060028   

            dc_score_none_size_intensity  dc_score_none_intensity  \
village_id                                                          
60683.0                       174.092005                 1.349222   
58270.0                       184.255885                 0.767768   
58278.0                       186.664125                 0.699896   
58297.0                       184.998387                 0.606656   
58269.0                       186.505368                 0.923385   
...                                  ...                      ...   
335320.0                        7.396460                 0.022056   
335170.0                        2.662398                 0.008577   
335315.0                       10.796235                 0.034234   
318467.0                        3.651472                 0.010622   
318465.0                        3.061057                 0.010201   

            dc_score_log_none  dc_score_log_size  dc_score_log_size_intensity  \
village_id                                                                      
60683.0             -2.905664           1.227887                     5.159584   
58270.0             -2.448230           1.284628                     5.216325   
58278.0             -2.729963           1.297614                     5.229311   
58297.0             -2.641268           1.288650                     5.220347   
58269.0             -2.428800           1.296763                     5.228460   
...                       ...                ...                          ...   
335320.0            -8.051204          -1.930696                     2.001002   
335170.0            -9.345976          -2.952470                     0.979227   
335315.0            -7.623550          -1.604978                     2.379197   
318467.0            -9.026517          -2.636567                     1.295130   
318465.0            -9.188718          -2.812937                     1.118760   

            dc_score_log_intensity  dc_score_sqrt_none  dc_score_sqrt_size  \
village_id                                                                   
60683.0                   0.299528            0.233907            1.847703   
58270.0                  -0.264268            0.294018            1.900875   
58278.0                  -0.356824            0.255385            1.913257   
58297.0                  -0.499793            0.266966            1.904701   
58269.0                  -0.079709            0.296888            1.912443   
...                            ...                 ...                 ...   
335320.0                 -3.814154            0.017853            0.380851   
335170.0                 -4.758670            0.009344            0.228496   
335315.0                 -3.374540            0.022109            0.448212   
318467.0                 -4.544860            0.010963            0.267594   
318465.0                 -4.585255            0.010109            0.245007   

            ...  dc_score_sqrt_intensity  dc_score_none_size_only  \
village_id  ...                                                     
60683.0     ...                 1.161560               724.148230   
58270.0     ...                 0.876223               724.148230   
58278.0     ...                 0.836598               724.148230 